# Discrepancies report of allowances data

### Add local path

In [1]:
import sys
sys.path.append('../')

### Imports

In [2]:
import plotly.express as px
import pandas as pd
import numpy as np
import json
from ydata_profiling import ProfileReport
from utils.preprocessor import Preprocessor
from data.events.allowance import allowance_events
from data.backend.allowance import allowance_backend
from data.backend.payment_schedule import payment_schedule_backend

2025-01-07 21:32:37.680 | INFO     | utils.preprocessor:load_json:41 - Loaded json file from ../data/files/allowance_events.json.
2025-01-07 21:32:37.687 | INFO     | utils.preprocessor:load_csv:59 - Loaded csv file from ../data/files/allowance_backend_table.csv.
2025-01-07 21:32:37.689 | INFO     | utils.preprocessor:load_csv:59 - Loaded csv file from ../data/files/payment_schedule_backend_table.csv.


## Table individual discrepancies analysis

### Allowance backend

Stores the current allowance settings for each user, reflecting their most recent allowance configuration.

In [3]:
allowance_backend.head()

user_uuid  creation_date frequency  \
0  30f4e25e-3e37-462e-8c3c-42f24f54350f     1724838709   monthly   
1  6da398ad-079d-49b9-8668-6d7ce4d22683     1724659829   monthly   
2  2d30fe2d-6c32-4b8a-a19b-906184f64f62     1731309159   monthly   
3  c30180f3-b35c-470c-b25a-f12ec4ce3340     1725414982   monthly   
4  9f5768db-e953-4057-9fa5-264c46293fbd     1726267511  biweekly   

             day                      updated_at  next_payment_day    status  
0  fifteenth_day  2024-10-15T08:00:41.445627563Z                15   enabled  
1  fifteenth_day                      1724659829                15   enabled  
2  fifteenth_day                      1731309159                15   enabled  
3      first_day  2024-10-01T08:00:37.516552581Z                 1   enabled  
4         friday   2024-10-02T02:33:10.97923183Z                11  disabled

In [4]:
allowance_backend.dtypes

user_uuid           object
creation_date        int64
frequency           object
day                 object
updated_at          object
next_payment_day     int64
status              object
dtype: object

Check duplicated user fields with **enabled** status

In [5]:
active_status_filter = (allowance_backend["status"] == "enabled")
equal_rows = allowance_backend[active_status_filter]["user_uuid"].nunique() == allowance_backend[active_status_filter].shape[0]

if equal_rows:
    print("All users have ONLY one allowance current setting, total rows: ", allowance_backend[active_status_filter].shape[0])

else:
    raise(Exception("There are some users with multiple allowances"))


All users have ONLY one allowance current setting, total rows:  2119


Check columns and values

In [6]:
allowance_backend_profile = ProfileReport(allowance_backend, title="Allowance Backend Profiling Report", explorative=True)
allowance_backend_profile.to_notebook_iframe()

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

**Table Report**
- The `updated_at` field has inconsistency across values with multiple formats
    - Examples:
        - Timestamp: `445627563Z`
        - Datetime: `2024-10-15T08:00:41`
- The `user_uuid` field uniquely identifies each user in the dataset.  
- The `payment_day` field ranges from 1 to 31, representing the possible days within a calendar month.  
- There is a correlation of **0.38** between the `next_payment_day` and `day` fields, which aligns with expected patterns in the data.  

### Allowance events

In [7]:
allowance_events.head()

user_uuid      event_timestamp event_name  \
0  03c5ffe8-6cd2-434b-a1b2-c4006860d94c   2024-09-21 1:39:34    created   
1  03c5ffe8-6cd2-434b-a1b2-c4006860d94c  2024-09-22 19:38:22     edited   
2  03c5ffe8-6cd2-434b-a1b2-c4006860d94c  2024-09-22 19:38:22     edited   
3  05384674-4af8-4f70-8d8f-90e19b0db971   2024-10-06 6:32:28    created   
4  05384674-4af8-4f70-8d8f-90e19b0db971   2024-10-06 6:32:37     edited   

  allowance_scheduled_frequency allowance_scheduled_day  allowance_amount  
0                        weekly                  sunday                10  
1                        weekly                  sunday                10  
2                        weekly                  sunday                10  
3                      biweekly                  friday                10  
4                        weekly                  friday                10

In [8]:
allowance_events.dtypes

user_uuid                        object
event_timestamp                  object
event_name                       object
allowance_scheduled_frequency    object
allowance_scheduled_day          object
allowance_amount                  int64
dtype: object

Check users from events that are not in the backend

In [9]:
print("Number of users that exist in the events but not in the backend: ", allowance_events[~allowance_events["user_uuid"].isin(allowance_backend["user_uuid"])]["user_uuid"].nunique())

Number of users that exist in the events but not in the backend:  2


In [10]:
allowance_events[~allowance_events["user_uuid"].isin(allowance_backend["user_uuid"])]

user_uuid      event_timestamp event_name  \
697   1cf825ad-c6fc-4881-9df1-20b495f375d8   2024-09-20 6:32:02    created   
5830  f0c58b79-2e41-4487-970f-fe6206bbe20b  2024-09-11 14:37:06    created   

     allowance_scheduled_frequency allowance_scheduled_day  allowance_amount  
697                       biweekly                  monday                20  
5830                       monthly           fifteenth_day                20

Check users from backend that are not in the events

In [11]:
print("Number of user that exist in the backend but not in the events: ", allowance_backend[~allowance_backend["user_uuid"].isin(allowance_events["user_uuid"])]["user_uuid"].nunique())

Number of user that exist in the backend but not in the events:  5


In [12]:
allowance_backend[~allowance_backend["user_uuid"].isin(allowance_events["user_uuid"])]

user_uuid  creation_date frequency        day  \
249  bb950bcb-0760-417d-888b-c4a99222d4a4     1726887192    weekly     friday   
745  59a14e2a-27a1-4cbd-9d30-46d2544af829     1732398605   monthly  first_day   
746  a616b4c6-482d-4e54-81c8-e6351de52c0f     1732398576   monthly  first_day   
747  a6ca6993-3b73-4a84-aa4f-4610b18dd91d     1732398568   monthly  first_day   
748  cd2d5904-7ca0-4d00-bdea-73bfbd3b56de     1732398587   monthly  first_day   

                         updated_at  next_payment_day   status  
249                      1726887192                27  enabled  
745  2024-12-01T08:00:32.291234184Z                 1  enabled  
746  2024-12-01T08:01:44.187981997Z                 1  enabled  
747  2024-12-01T08:01:43.387951119Z                 1  enabled  
748                      1732398587                 1  enabled

In [13]:
allowance_events_profile = ProfileReport(allowance_events, title="Allowance Events Profiling Report", explorative=True)
allowance_events_profile.to_notebook_iframe()

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

Analyze events per day and apparent duplicated rows

From the Profile Report I see that the number of events increased from one day to another. In another context this would be something to investigate, as here it is a source of truth I will just visualize it and continue.

In [14]:
duplicate_rows = allowance_events[allowance_events.duplicated(subset=["user_uuid", "event_timestamp"], keep=False)]
duplicate_rows["event_timestamp"] = pd.to_datetime(duplicate_rows["event_timestamp"])
duplicate_rows_per_day = duplicate_rows["event_timestamp"].dt.date.value_counts().sort_index()

/var/folders/5s/tkklx12s0m73jfrzpxd14tn40000gp/T/ipykernel_24131/513895178.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  duplicate_rows["event_timestamp"] = pd.to_datetime(duplicate_rows["event_timestamp"])


In [15]:
print("Number of duplicate rows in the events data:", duplicate_rows.shape[0], "of", allowance_events.shape[0])

Number of duplicate rows in the events data: 2028 of 6208


In [16]:
# Get lenght of the period to corresponde 1 bin = 1 day
allowance_events["event_timestamp"] = pd.to_datetime(allowance_events["event_timestamp"])
number_days = (allowance_events["event_timestamp"].max() - allowance_events["event_timestamp"].min()).days

print("Number of days in the events data: ", number_days)

Number of days in the events data:  130


In [17]:
fig = px.histogram(
    allowance_events, 
    x="event_timestamp", 
    nbins=number_days,
    title="Number of Events Over Time",
    labels={"event_timestamp": "Event Timestamp", "count": "Number of Events"},
    color_discrete_sequence=["#1f77b4"]
)

fig.add_trace(
    px.line(
        x=duplicate_rows_per_day.index, 
        y=duplicate_rows_per_day.values, 
        labels={"x": "Event Timestamp", "y": "Number of Duplicated Events"},
        color_discrete_sequence=["#ff7f0e"]
    ).data[0]
)

fig.update_layout(
    xaxis_title="Event Timestamp",
    yaxis_title="Number of Events",
    title_x=0.5,
    template="plotly_white" 
)

fig.show()

**Table Report**  
- The table contains **16.3%** of apparent duplicated rows, but we need to consider the possibility of legitimate repeated events because is the source of truth.
- The number of events increased significantly starting from **September 2nd**. Considering that this table is the source of truth, this increase could be attributed to higher usage driven by campaigns, seasonality, or other factors. Also, the apparent duplicated rows could be related to the same cause.

### Payment schedule backend

In [18]:
payment_schedule_backend.head(10)

user_uuid  payment_date
0  061d8039-b332-40ca-b906-3514b06411c2            22
1  0ca92d01-feed-42e5-b90c-299b615f9d3f            22
2  160bcd2d-3ab0-4a60-9bfa-ccfcc1ee17e4            22
3  1649fee7-c424-4fb7-ac84-db36e15e042a            22
4  1d647703-874d-4744-b4de-6a5212518aa8            22
5  2026a912-d221-42bf-9d4b-ebcf1b9ba02c            22
6  298b9863-9dca-4f31-b35c-7e19ce678e5e            22
7  2b0e5667-52e4-40cf-a4dd-c0218d6b7574            22
8  2bf2d121-9076-450d-a9e3-3fe6c83dba91            22
9  2db8f773-9e65-4200-bbf2-edc4994435a4            22

In [19]:
payment_schedule_backend.dtypes

user_uuid       object
payment_date     int64
dtype: object

In [20]:
print("Distinct user uuid:", payment_schedule_backend["user_uuid"].nunique())

Distinct user uuid: 2126


In [21]:
print("Distinct rows:", payment_schedule_backend.shape[0])

Distinct rows: 2139


In [22]:
duplicated_user_rows = payment_schedule_backend[payment_schedule_backend.duplicated(subset=["user_uuid"], keep=False)].sort_values(by="user_uuid")

In [23]:
duplicated_user_rows

user_uuid  payment_date
1575  172fe923-347e-4d0e-ba82-1e9969aaadde            11
1629  172fe923-347e-4d0e-ba82-1e9969aaadde             3
1498  19d933a6-2810-4c08-b3d6-d68ef3c6eac3             7
1178  19d933a6-2810-4c08-b3d6-d68ef3c6eac3            28
972   42f61042-3d31-42ff-9f1a-508716069464             6
1652  42f61042-3d31-42ff-9f1a-508716069464            20
1384  72190913-1208-4333-aaf4-ea7d04dccacd             4
1592  72190913-1208-4333-aaf4-ea7d04dccacd            11
2119  72e8fe3f-0dd9-44e3-8775-660bacb17310            14
239   72e8fe3f-0dd9-44e3-8775-660bacb17310            13
1310  72e8fe3f-0dd9-44e3-8775-660bacb17310             5
2005  77cdda96-6e5b-47c1-b486-9f06da2c7372            15
701   77cdda96-6e5b-47c1-b486-9f06da2c7372             1
739   9221dccf-44f3-446d-b3ce-19f9123ea627             1
1598  9221dccf-44f3-446d-b3ce-19f9123ea627            11
1606  abf5cf1e-e81a-4b5f-9d5b-649fa10d8f81            11
1639  abf5cf1e-e81a-4b5f-9d5b-649fa10d8f81             3
1106  c091a91b-c6fd-44cb-8ac7-fe3fdbafccea             6
1543  c091a91b-c6fd-44cb-8ac7-fe3fdbafccea             7
95    d299d804-0d05-48c8-ad62-601d54438e34            18
1274  d299d804-0d05-48c8-ad62-601d54438e34            27
1712  d769685e-9046-4ffe-a51d-829ec7f1d877            29
1785  d769685e-9046-4ffe-a51d-829ec7f1d877            25
1892  eab4d50f-2a17-4f07-b462-53be0e54f6c6            10
1567  eab4d50f-2a17-4f07-b462-53be0e54f6c6             7

In [24]:
print("Number of duplicated users:", duplicated_user_rows["user_uuid"].nunique())

Number of duplicated users: 12


Check if the backend users with status `disable` have an active record in the scheduled payment table

In [25]:
backend_disabled_filter = (allowance_backend["status"] == "disabled")
backend_disabled_users = list(allowance_backend[backend_disabled_filter]["user_uuid"].unique())

In [26]:
disabled_users_with_payments = len(payment_schedule_backend[payment_schedule_backend["user_uuid"].isin(backend_disabled_users)]["user_uuid"].unique())

In [27]:
print("Number of users with disabled allowance that have payments scheduled: ", disabled_users_with_payments)

Number of users with disabled allowance that have payments scheduled:  5


In [28]:
payment_schedule_backend[payment_schedule_backend["user_uuid"].isin(backend_disabled_users)].sort_values(by="user_uuid")

user_uuid  payment_date
199  10ce6301-64f6-49bb-989c-fea0d3d5334f            13
960  38f33888-4f29-4dc5-80bc-15650c93b32b             6
182  7d108518-4d87-4b6a-857a-8b37772c75e6             2
29   9d82a047-27a3-4841-9ffa-c85c5308ee6a            22
40   e359dbab-86cf-4576-8d16-3c08df3f6a41            22

**Table Report**  
- There are **12 users** with duplicated rows, which is incorrect because each user should have only one row.  
- Users with a backend status of `disable` have an active record in the scheduled payment table. These users should not have any active records.  

### **Conclusions** from individual table analysis

- The **Allowance Backend Table** demonstrates unique user identifiers and expected correlations between payment days, providing a reliable foundation for payment scheduling models and user-level analyses. Thorough the `updated_at` field exhibits inconsistencies, with values stored in multiple formats:
  - Timestamp: `445627563Z`  
  - Datetime: `2024-10-15T08:00:41`
If the backend team is using this field for any purpose, it is recommended to standardize the format to ensure data consistency and facilitate payment date calculation.

- The **Allowance Events Table** shows a **16.3% duplication rate**, which may indicate either legitimate repeated events or data redundancy. The event surge beginning on **September 2nd** suggests this increase is tied to seasonal trends, campaigns, or higher platform engagement rather than solely data integrity issues. Further inspection is necessary to distinguish between valid events and duplicates. For now we will consider this table as the source of truth.


- The **Payment Schedule Backend Table** contains critical data quality issues, including duplicated user rows and incorrectly active payment records for users with a `disable` status. These flaws risk compromising payment processing, potentially causing financial inaccuracies and rule violations.  


- The correlation between **next_payment_day** and **day** in the **Allowance Backend Table** indicates that payment patterns are logical and predictable, but the systemic errors in scheduling data require immediate action to ensure operational reliability.  


- Addressing the duplication and status-related inconsistencies across these tables is essential to enhance data accuracy, safeguard financial processes, and improve overall system performance.

## Payment date cases inconsistencies

### Join backend data

The `payment_date` values from **payment_schedule_backend** should align with the `next_payment_day` from the **allowance_backend_table**.

Merge **enabled** backend allowances settings with the payment schedule

In [29]:
active_status_filter = (allowance_backend['status'] == 'enabled')
enabled_backend_allowances = allowance_backend[active_status_filter]

In [30]:
payments = pd.merge(enabled_backend_allowances, payment_schedule_backend, on="user_uuid", how="left")
payments["abs_days_difference"] = abs(payments["payment_date"] - payments["next_payment_day"])
payments['updated_at'] = payments['updated_at'].apply(Preprocessor.parse_date)
payments['updated_week_day'] = payments['updated_at'].dt.day_name().str.lower()

In [31]:
payments.head()

user_uuid  creation_date frequency  \
0  30f4e25e-3e37-462e-8c3c-42f24f54350f     1724838709   monthly   
1  6da398ad-079d-49b9-8668-6d7ce4d22683     1724659829   monthly   
2  2d30fe2d-6c32-4b8a-a19b-906184f64f62     1731309159   monthly   
3  c30180f3-b35c-470c-b25a-f12ec4ce3340     1725414982   monthly   
4  35d3d7c2-2a05-4eae-bdf2-7896e611bbc6     1725453772  biweekly   

             day                          updated_at  next_payment_day  \
0  fifteenth_day 2024-10-15 08:00:41.445627563+00:00                15   
1  fifteenth_day           2024-08-26 08:10:29+00:00                15   
2  fifteenth_day           2024-11-11 07:12:39+00:00                15   
3      first_day 2024-10-01 08:00:37.516552581+00:00                 1   
4         monday           2024-09-04 12:42:52+00:00                16   

    status  payment_date  abs_days_difference updated_week_day  
0  enabled            15                    0          tuesday  
1  enabled            15                    0           monday  
2  enabled            15                    0           monday  
3  enabled             1                    0          tuesday  
4  enabled            16                    0        wednesday

Filter inconsistencies between the `payment_date` and `next_payment_day` fields

In [32]:
different_payment_filter = (payments["abs_days_difference"] >= 1)
inconsistent_payments = payments[different_payment_filter]

In [33]:
inconsistent_payments.head()

user_uuid  creation_date frequency        day  \
103  a87ead42-0f1b-4f29-8bcf-752c53994a86     1726442165  biweekly     friday   
145  77cdda96-6e5b-47c1-b486-9f06da2c7372     1729432012   monthly  first_day   
276  b8ac9de0-9629-403c-a0a2-f53592e4f753     1727285025    weekly     friday   
317  72e8fe3f-0dd9-44e3-8775-660bacb17310     1726083350    weekly   thursday   
319  72e8fe3f-0dd9-44e3-8775-660bacb17310     1726083350    weekly   thursday   

                             updated_at  next_payment_day   status  \
103 2024-10-28 12:34:06.316880286+00:00                 8  enabled   
145 2024-12-01 08:00:40.299599397+00:00                 1  enabled   
276 2024-10-12 16:11:16.953198194+00:00                18  enabled   
317 2024-11-28 08:00:24.576417825+00:00                 5  enabled   
319 2024-11-28 08:00:24.576417825+00:00                 5  enabled   

     payment_date  abs_days_difference updated_week_day  
103            25                   17           monday  
145            15                   14           sunday  
276            27                    9         saturday  
317            13                    8         thursday  
319            14                    9         thursday

In [34]:
print("Number of users with inconsistent  payment dates in the backend:", len(inconsistent_payments["user_uuid"].unique()), "from", len(enabled_backend_allowances["user_uuid"].unique()))

Number of users with inconsistent  payment dates in the backend: 52 from 2119


In [35]:
print("Number of Inconsistent payment dates in the backend:", len(inconsistent_payments), "from", len(payments))

Number of Inconsistent payment dates in the backend: 53 from 2132


In [36]:
print("Different Inconsistent payment dates frequency period:")
print(inconsistent_payments["frequency"].value_counts())

Different Inconsistent payment dates frequency period:
frequency
weekly      33
biweekly    17
daily        2
monthly      1
Name: count, dtype: int64


In [37]:
print(f"We have inconsistencies in all frequency periods EXCEPT: {list(set(payments['frequency'].value_counts().index) - set(inconsistent_payments['frequency'].value_counts().index))}")

We have inconsistencies in all frequency periods EXCEPT: []


In [38]:
print("Different frequency day with inconsistecies:")
print(inconsistent_payments["day"].value_counts())

Different frequency day with inconsistecies:
day
friday       24
wednesday     7
thursday      6
monday        5
tuesday       3
saturday      3
daily         2
sunday        2
first_day     1
Name: count, dtype: int64


In [39]:
print(f"We have inconsistencies in all frequency days EXCEPT: {list(set(payments['day'].value_counts().index) - set(inconsistent_payments['day'].value_counts().index))}")

We have inconsistencies in all frequency days EXCEPT: ['fifteenth_day']


In [40]:
print(f"The maiority of the inconsistent payment dates are during: {inconsistent_payments['day'].value_counts().index[0]}")

The maiority of the inconsistent payment dates are during: friday


### Join events data *(source of truth)*

In [41]:
allowance_events.head()

user_uuid     event_timestamp event_name  \
0  03c5ffe8-6cd2-434b-a1b2-c4006860d94c 2024-09-21 01:39:34    created   
1  03c5ffe8-6cd2-434b-a1b2-c4006860d94c 2024-09-22 19:38:22     edited   
2  03c5ffe8-6cd2-434b-a1b2-c4006860d94c 2024-09-22 19:38:22     edited   
3  05384674-4af8-4f70-8d8f-90e19b0db971 2024-10-06 06:32:28    created   
4  05384674-4af8-4f70-8d8f-90e19b0db971 2024-10-06 06:32:37     edited   

  allowance_scheduled_frequency allowance_scheduled_day  allowance_amount  
0                        weekly                  sunday                10  
1                        weekly                  sunday                10  
2                        weekly                  sunday                10  
3                      biweekly                  friday                10  
4                        weekly                  friday                10

In [42]:
allowance_events["event_timestamp"] = pd.to_datetime(allowance_events["event_timestamp"])
allowance_events["hours_between_events"] = allowance_events.groupby("user_uuid")["event_timestamp"].diff().dt.total_seconds() / 3600

Group allowances events data

In [43]:
# group and add total_events and total_amount column
grouped_allowance_events = allowance_events.groupby("user_uuid").agg(
    total_events=pd.NamedAgg(column="event_timestamp", aggfunc="count"),
    distinct_events=pd.NamedAgg(column="event_timestamp", aggfunc="nunique"),
    sum_amount=pd.NamedAgg(column="allowance_amount", aggfunc="sum"),
    distinct_frequency=pd.NamedAgg(column="allowance_scheduled_frequency", aggfunc="nunique"),
    distinct_scheduled_days=pd.NamedAgg(column="allowance_scheduled_day", aggfunc="nunique"),
)

In [44]:
grouped_allowance_events.head()

total_events  distinct_events  \
user_uuid                                                             
00039f90-7331-401c-bcf1-72a4a9c42a18             1                1   
00139bdc-92b3-4ebd-af94-285acf2fd376             2                2   
0035bbe5-5034-40b6-aa8f-b50047f09dea             5                3   
004e441f-6f3f-425b-b450-eac1593495a0             3                3   
0062bb03-fe16-45d6-96bb-67099c53299a             1                1   

                                      sum_amount  distinct_frequency  \
user_uuid                                                              
00039f90-7331-401c-bcf1-72a4a9c42a18           5                   1   
00139bdc-92b3-4ebd-af94-285acf2fd376          40                   1   
0035bbe5-5034-40b6-aa8f-b50047f09dea          25                   1   
004e441f-6f3f-425b-b450-eac1593495a0          15                   2   
0062bb03-fe16-45d6-96bb-67099c53299a         100                   1   

                                      distinct_scheduled_days  
user_uuid                                                      
00039f90-7331-401c-bcf1-72a4a9c42a18                        1  
00139bdc-92b3-4ebd-af94-285acf2fd376                        2  
0035bbe5-5034-40b6-aa8f-b50047f09dea                        3  
004e441f-6f3f-425b-b450-eac1593495a0                        2  
0062bb03-fe16-45d6-96bb-67099c53299a                        1

Analyze **all payment dates**

In [45]:
payments_profile = ProfileReport(payments, title="Allowance payments Profiling Report", explorative=True)
payments_profile.to_notebook_iframe()

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

Analyze **inconsistent payment dates**

In [46]:
inconsistent_payments_profile = ProfileReport(inconsistent_payments, title="Allowance inconsistent payments Profiling Report", explorative=True)
inconsistent_payments_profile.to_notebook_iframe()

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

In [47]:
payments_with_grouped_events = pd.merge(payments, grouped_allowance_events, on="user_uuid", how="left")
inconsistent_payments_with_grouped_events = pd.merge(inconsistent_payments, grouped_allowance_events, on="user_uuid", how="left")

In [48]:
inconsistent_payments_with_grouped_events.head()

user_uuid  creation_date frequency        day  \
0  a87ead42-0f1b-4f29-8bcf-752c53994a86     1726442165  biweekly     friday   
1  77cdda96-6e5b-47c1-b486-9f06da2c7372     1729432012   monthly  first_day   
2  b8ac9de0-9629-403c-a0a2-f53592e4f753     1727285025    weekly     friday   
3  72e8fe3f-0dd9-44e3-8775-660bacb17310     1726083350    weekly   thursday   
4  72e8fe3f-0dd9-44e3-8775-660bacb17310     1726083350    weekly   thursday   

                           updated_at  next_payment_day   status  \
0 2024-10-28 12:34:06.316880286+00:00                 8  enabled   
1 2024-12-01 08:00:40.299599397+00:00                 1  enabled   
2 2024-10-12 16:11:16.953198194+00:00                18  enabled   
3 2024-11-28 08:00:24.576417825+00:00                 5  enabled   
4 2024-11-28 08:00:24.576417825+00:00                 5  enabled   

   payment_date  abs_days_difference updated_week_day  total_events  \
0            25                   17           monday            13   
1            15                   14           sunday             5   
2            27                    9         saturday             3   
3            13                    8         thursday            44   
4            14                    9         thursday            44   

   distinct_events  sum_amount  distinct_frequency  distinct_scheduled_days  
0                7          81                   1                        2  
1                5          50                   2                        2  
2                3         100                   1                        1  
3               32        7669                   2                        7  
4               32        7669                   2                        7

In [49]:
inconsistent_payments_with_grouped_events["total_events"].describe()

count    53.000000
mean      6.679245
std       8.076018
min       2.000000
25%       3.000000
50%       5.000000
75%       7.000000
max      44.000000
Name: total_events, dtype: float64

In [50]:
print(f"Users with wrong payment dates had at least {inconsistent_payments_with_grouped_events['total_events'].min()} events in their history.")

Users with wrong payment dates had at least 2 events in their history.


Join grouped data with the wrong payments cases

In [51]:
payments_with_grouped_events = pd.merge(payments, grouped_allowance_events, on="user_uuid", how="left")
inconsistent_payments_with_grouped_events = pd.merge(inconsistent_payments, grouped_allowance_events, on="user_uuid", how="left")

In [52]:
inconsistent_payments_with_grouped_events.head()

user_uuid  creation_date frequency        day  \
0  a87ead42-0f1b-4f29-8bcf-752c53994a86     1726442165  biweekly     friday   
1  77cdda96-6e5b-47c1-b486-9f06da2c7372     1729432012   monthly  first_day   
2  b8ac9de0-9629-403c-a0a2-f53592e4f753     1727285025    weekly     friday   
3  72e8fe3f-0dd9-44e3-8775-660bacb17310     1726083350    weekly   thursday   
4  72e8fe3f-0dd9-44e3-8775-660bacb17310     1726083350    weekly   thursday   

                           updated_at  next_payment_day   status  \
0 2024-10-28 12:34:06.316880286+00:00                 8  enabled   
1 2024-12-01 08:00:40.299599397+00:00                 1  enabled   
2 2024-10-12 16:11:16.953198194+00:00                18  enabled   
3 2024-11-28 08:00:24.576417825+00:00                 5  enabled   
4 2024-11-28 08:00:24.576417825+00:00                 5  enabled   

   payment_date  abs_days_difference updated_week_day  total_events  \
0            25                   17           monday            13   
1            15                   14           sunday             5   
2            27                    9         saturday             3   
3            13                    8         thursday            44   
4            14                    9         thursday            44   

   distinct_events  sum_amount  distinct_frequency  distinct_scheduled_days  
0                7          81                   1                        2  
1                5          50                   2                        2  
2                3         100                   1                        1  
3               32        7669                   2                        7  
4               32        7669                   2                        7

In [53]:
inconsistent_payments_with_grouped_events["total_events"].describe()

count    53.000000
mean      6.679245
std       8.076018
min       2.000000
25%       3.000000
50%       5.000000
75%       7.000000
max      44.000000
Name: total_events, dtype: float64

In [54]:
print(f"Users with wrong payment dates had at least {inconsistent_payments_with_grouped_events['total_events'].min()} events in their history.")

Users with wrong payment dates had at least 2 events in their history.


Visualize inconsistencies in **specific cases**

In [55]:
inconsistent_users = list(inconsistent_payments["user_uuid"].unique())
sample_user = np.random.choice(inconsistent_users)

print("Sample user UUID:", sample_user)

Sample user UUID: c091a91b-c6fd-44cb-8ac7-fe3fdbafccea


In [56]:
allowance_events[allowance_events["user_uuid"] == sample_user].sort_values(by="event_timestamp")

user_uuid     event_timestamp event_name  \
1363  c091a91b-c6fd-44cb-8ac7-fe3fdbafccea 2024-10-05 08:48:16    created   
1364  c091a91b-c6fd-44cb-8ac7-fe3fdbafccea 2024-10-05 08:49:51     edited   
1365  c091a91b-c6fd-44cb-8ac7-fe3fdbafccea 2024-10-05 08:49:52     edited   
1366  c091a91b-c6fd-44cb-8ac7-fe3fdbafccea 2024-10-05 08:51:51     edited   
1367  c091a91b-c6fd-44cb-8ac7-fe3fdbafccea 2024-10-05 08:51:51     edited   
1368  c091a91b-c6fd-44cb-8ac7-fe3fdbafccea 2024-10-20 10:06:29     edited   
1369  c091a91b-c6fd-44cb-8ac7-fe3fdbafccea 2024-10-20 10:06:29     edited   
1371  c091a91b-c6fd-44cb-8ac7-fe3fdbafccea 2024-10-27 20:20:51     edited   
1370  c091a91b-c6fd-44cb-8ac7-fe3fdbafccea 2024-10-27 20:20:51     edited   
1372  c091a91b-c6fd-44cb-8ac7-fe3fdbafccea 2024-10-27 20:21:43     edited   
1373  c091a91b-c6fd-44cb-8ac7-fe3fdbafccea 2024-10-27 20:21:43     edited   
1374  c091a91b-c6fd-44cb-8ac7-fe3fdbafccea 2024-10-30 14:25:32     edited   
1375  c091a91b-c6fd-44cb-8ac7-fe3fdbafccea 2024-10-30 14:25:32     edited   
1376  c091a91b-c6fd-44cb-8ac7-fe3fdbafccea 2024-10-30 16:56:54     edited   
1377  c091a91b-c6fd-44cb-8ac7-fe3fdbafccea 2024-10-30 16:56:54     edited   
1379  c091a91b-c6fd-44cb-8ac7-fe3fdbafccea 2024-11-13 06:09:45     edited   
1378  c091a91b-c6fd-44cb-8ac7-fe3fdbafccea 2024-11-13 06:09:45     edited   
1380  c091a91b-c6fd-44cb-8ac7-fe3fdbafccea 2024-11-28 13:34:15     edited   

     allowance_scheduled_frequency allowance_scheduled_day  allowance_amount  \
1363                      biweekly                thursday                20   
1364                         daily                   daily                20   
1365                         daily                   daily                20   
1366                      biweekly                  friday                20   
1367                      biweekly                  friday                20   
1368                       monthly               first_day                10   
1369                       monthly               first_day                10   
1371                       monthly               first_day                35   
1370                       monthly               first_day                35   
1372                       monthly               first_day                36   
1373                       monthly               first_day                36   
1374                      biweekly                  friday                57   
1375                      biweekly                  friday                57   
1376                      biweekly                thursday                57   
1377                      biweekly                thursday                57   
1379                      biweekly                thursday                 5   
1378                      biweekly                thursday                 5   
1380                        weekly                  friday                95   

      hours_between_events  
1363                   NaN  
1364              0.026389  
1365              0.000278  
1366              0.033056  
1367              0.000000  
1368            361.243889  
1369              0.000000  
1371              0.000000  
1370            178.239444  
1372              0.014444  
1373              0.000000  
1374             66.063611  
1375              0.000000  
1376              2.522778  
1377              0.000000  
1379              0.000000  
1378            325.214167  
1380            367.408333

In [57]:
allowance_backend[allowance_backend["user_uuid"] == sample_user]

user_uuid  creation_date frequency     day  \
2576  c091a91b-c6fd-44cb-8ac7-fe3fdbafccea     1728143296    weekly  friday   

                          updated_at  next_payment_day   status  
2576  2024-11-29T08:00:36.260812719Z                 6  enabled

In [58]:
payment_schedule_backend[payment_schedule_backend["user_uuid"] == sample_user]

user_uuid  payment_date
1106  c091a91b-c6fd-44cb-8ac7-fe3fdbafccea             6
1543  c091a91b-c6fd-44cb-8ac7-fe3fdbafccea             7

In [59]:
inconsistent_payments[inconsistent_payments["user_uuid"] == sample_user]

user_uuid  creation_date frequency     day  \
1903  c091a91b-c6fd-44cb-8ac7-fe3fdbafccea     1728143296    weekly  friday   

                              updated_at  next_payment_day   status  \
1903 2024-11-29 08:00:36.260812719+00:00                 6  enabled   

      payment_date  abs_days_difference updated_week_day  
1903             7                    1           friday

After reviewing specific users, I found that the `updated_at` field is not correlated with the `last_event` from our source of truth. I would like to investigate this issue more thoroughly 👇

Check update delay in inconsistency cases

In [60]:
# Get last event per user
last_events = allowance_events.groupby("user_uuid")["event_timestamp"].last().reset_index()
last_events.rename(columns={"event_timestamp": "last_event_at"}, inplace=True)
last_events.head()

user_uuid       last_event_at
0  00039f90-7331-401c-bcf1-72a4a9c42a18 2024-10-01 12:42:35
1  00139bdc-92b3-4ebd-af94-285acf2fd376 2024-10-29 13:19:42
2  0035bbe5-5034-40b6-aa8f-b50047f09dea 2024-09-28 06:49:22
3  004e441f-6f3f-425b-b450-eac1593495a0 2024-09-25 15:39:34
4  0062bb03-fe16-45d6-96bb-67099c53299a 2024-08-24 10:44:20

In [61]:
# Ensure last_event_at is timezone-aware
last_events["last_event_at"] = last_events["last_event_at"].dt.tz_localize('UTC')

inconsistent_payments_with_last_events = pd.merge(inconsistent_payments, last_events, on="user_uuid", how="left")
inconsistent_payments_with_last_events["delta_hour_last_event_updated_at"] = round((inconsistent_payments_with_last_events["updated_at"] - inconsistent_payments_with_last_events["last_event_at"]).dt.total_seconds() / 3600)
inconsistent_payments_with_last_events["last_event_is_before"] = inconsistent_payments_with_last_events["last_event_at"] < inconsistent_payments_with_last_events["updated_at"]
inconsistent_payments_with_last_events.head()

user_uuid  creation_date frequency        day  \
0  a87ead42-0f1b-4f29-8bcf-752c53994a86     1726442165  biweekly     friday   
1  77cdda96-6e5b-47c1-b486-9f06da2c7372     1729432012   monthly  first_day   
2  b8ac9de0-9629-403c-a0a2-f53592e4f753     1727285025    weekly     friday   
3  72e8fe3f-0dd9-44e3-8775-660bacb17310     1726083350    weekly   thursday   
4  72e8fe3f-0dd9-44e3-8775-660bacb17310     1726083350    weekly   thursday   

                           updated_at  next_payment_day   status  \
0 2024-10-28 12:34:06.316880286+00:00                 8  enabled   
1 2024-12-01 08:00:40.299599397+00:00                 1  enabled   
2 2024-10-12 16:11:16.953198194+00:00                18  enabled   
3 2024-11-28 08:00:24.576417825+00:00                 5  enabled   
4 2024-11-28 08:00:24.576417825+00:00                 5  enabled   

   payment_date  abs_days_difference updated_week_day  \
0            25                   17           monday   
1            15                   14           sunday   
2            27                    9         saturday   
3            13                    8         thursday   
4            14                    9         thursday   

              last_event_at  delta_hour_last_event_updated_at  \
0 2024-10-28 05:34:06+00:00                               7.0   
1 2024-11-15 05:40:25+00:00                             386.0   
2 2024-10-12 09:11:17+00:00                               7.0   
3 2024-11-27 04:15:10+00:00                              28.0   
4 2024-11-27 04:15:10+00:00                              28.0   

   last_event_is_before  
0                  True  
1                  True  
2                  True  
3                  True  
4                  True

Check if the last event occurred before the inconsistency *(expected)*

In [62]:
print("Number of users with last event before the payment update:", len(inconsistent_payments_with_last_events[inconsistent_payments_with_last_events["last_event_is_before"]]))

Number of users with last event before the payment update: 53


In [63]:
print("Number of users with last event after the payment update:", len(inconsistent_payments_with_last_events[~inconsistent_payments_with_last_events["last_event_is_before"]]))

Number of users with last event after the payment update: 0


In [64]:
inconsistent_payments_with_last_events["delta_hour_last_event_updated_at"].describe()

count     53.000000
mean      24.886792
std       82.015866
min        7.000000
25%        7.000000
50%        8.000000
75%        8.000000
max      478.000000
Name: delta_hour_last_event_updated_at, dtype: float64

### **Conclusions** from the Discrepancies Between Payment Dates  

- **Delay in Payment Date Updates in Backend Allowance**:  
  In all observed cases, the last event occurred before the inconsistency, with a delay ranging from **at least 7 hours** to up to **478 hours (~20 days)**. This delay could be due to backend processing delays or errors in updating the payment date after an allowance change. The backend team should investigate the root cause of these delays to ensure timely and accurate payment date updates. This issue may contribute to discrepancies in payment dates calculation, as the delay in updating the payment date could lead to mismatches between the backend and events data.  

- **Minimum Two Events for Discrepancies**:  
  The presence of discrepancies in all cases involves at least two events, reinforcing the need to focus on **`allowance edited`** events. The initial creation event (`allowance created`) does not appear to be the source of the inconsistencies. This suggests that errors are happening during the **`update`** or **`delete+insert`** operations performed by the backend team. The backend tables should only reflect the most recent user settings, indicating the need for more effective data modification handling.  

- **Inconsistent Payment Dates in Backend Tables**:  
  A total of **52 users** out of **2119** and **53 payment dates** out of **2132** exhibit inconsistencies. While this issue is not widespread, it occurs frequently enough to warrant immediate attention. The slight difference in numbers (52 users vs. 53 dates) suggests that some users have more than one inconsistency.  

- **Inconsistencies Across All Days (Except Monthly/15th)**:  
  Inconsistencies are observed across all days, with the exception of monthly and 15th payments, indicating that the issue likely resides in the general payment date calculation logic used during updates. Monthly 15th payments may work correctly due to a simpler implementation or because edits are less frequent for this particular setting. Additionally, users with monthly/15th schedules may be less likely to change them, leading to fewer inconsistencies.  

- **Majority of Discrepancies on Friday**:  
  A clear pattern emerges where **Friday** payment schedules are the most affected by inconsistencies. This suggests a possible logic error related to the end-of-week transitions or weekly offsets. The backend code responsible for updating Friday allowances — or handling changes in weekly offsets — should be thoroughly examined.  

## Final

#### Conclusion

1. **Update Logic is the Primary Suspect:**
    All users with inconsistent payment dates have at least two events in their history, indicating the issue arises when allowances are *edited* (`allowance.edited` events), not during initial creation.  The backend team should prioritize investigating the code responsible for updating `next_payment_day` and `payment_date` after edits.

2. **Backend Update Delays:**
    There are significant delays (7+ hours, up to 20 days) between when an `allowance.edited` event occurs and when the backend tables are updated. This delay could be a contributing factor to discrepancies and should be investigated and resolved to ensure timely updates and accurate payment processing.

3. **Focus on Weekly and Biweekly Friday Schedules:**
    The *vast majority* of discrepancies involve weekly and biweekly allowances scheduled for Friday.  A deep dive into the update logic for these cases is crucial. The code likely contains errors related to day-of-week calculations, week transitions (across weekends), or applying correct time deltas when shifting to or from Friday. Edits on `biweekly` seem to use an incorrect logic for next payment day, potentially inheriting the error from `weekly`.

4. **Examine Biweekly Allowances Edits:**
    In some cases, edit logic for biweekly allowances produces multiple inconsistent records in the `payment_schedule_backend_table` *or* incorrect values for `next_payment_day`, sometimes moving the payment back 1 day, other times 3. This suggests inconsistencies or possibly race conditions in this part of the code.

5. **Data Inconsistencies in Allowance Backend Table:** 
    The `updated_at` field in `allowance_backend_table` has inconsistent data types. While not a direct cause of payment date errors, standardizing this field will improve overall data quality and might simplify debugging in the future.

#### Action items

1. **Code Review:**
    Prioritize reviewing the code responsible for `next_payment_day` calculations after `allowance.edited` events, particularly for weekly and biweekly allowances involving Friday.

2. **Test Cases:**
    Develop targeted test cases for weekly and biweekly allowances, with edits involving Friday or changing weekly offsets, to reproduce the reported discrepancies and ensure any fixes are correct.  Test cases for multiple `allowance.edited` events for the same user could expose errors in handling subsequent payment calculations after the first.

3. **Data Consistency:**
    Standardize the data type for the `updated_at` field in `allowance_backend_table`.

4. **Performance/Delay Investigation:**
    Address the delays in backend updates after `allowance.edited` events. Consider logging or tracing to identify bottlenecks or errors in the update process.